In [1]:
import spacy
import timeit
import math
import pandas as pd
import shutil
import matplotlib.pyplot as plt
from os import path
from collections import Counter
from lxml import etree
from glob import glob
from unicodedata import normalize

In [6]:
nlp = spacy.load('fr_core_news_lg')

In [16]:
path_name = r"../chunked_corpus_lemma_txt/*.txt"

In [10]:
def clean_text(txt):
    txt_res = normalize("NFKD", txt.replace('\xa0', ' '))
    txt_res = txt_res.replace('\\xa0', '')
    return txt_res

In [9]:
def pipeline_spacy(path):
    pos_ko = ["NUM", "X", "SYM", "PUNCT", "SPACE"]
    list_lemma = []
    list_pos = []
    nombre_tokens = 0
    with open(path, encoding="utf8") as file:
        text = file.readlines()
        text_clean = clean_text(str(text).lower())
        docs = nlp(text_clean)
        nombre_tokens += len(docs)
        for token in docs:
            #si le token est bien un mot on récupère son lemme
            if token.pos_ not in pos_ko:
                list_lemma.append(token.lemma_)
    return list_lemma, nombre_tokens

In [7]:
def bigrammize(list_token):
    """fonction qui prend en parametre une liste de tokens et retourne une liste de bi-grammes"""
    list_bigram = []
    for indice_token in range(len(list_token)-1):
        bigram = list_token[indice_token]+'_'+list_token[indice_token+1]
        list_bigram.append(bigram)
    return list_bigram

In [8]:
def dict_freq_token(list_select, list_lemma):
    
    dict_result = dict.fromkeys(list_select)
    
    dict_temp = Counter(list_lemma)
        
    for key in dict_temp.keys():
        if key in dict_result.keys():
            dict_result[key] = dict_temp[key]/len(list_lemma)
    
    return dict_result

In [14]:
lemma_selected

['le',
 'de',
 'un',
 'et',
 'il',
 'avoir',
 'à',
 'lui',
 'être',
 'son',
 'que',
 'l’',
 'ce',
 'je',
 'en',
 'd’',
 'qui',
 'pas',
 'ne',
 'vous',
 'se',
 'dans',
 'qu’',
 'tout',
 'pour',
 'faire',
 'dire',
 's’',
 'mon',
 'au',
 'éter',
 'n’',
 'sur',
 'plus',
 '-',
 'mais',
 'on',
 '–',
 'avec',
 'me',
 'par',
 'comme',
 'c’',
 'nous',
 'pouvoir',
 'si',
 'bien',
 'j’',
 'y',
 'voir',
 'aller',
 'même',
 'moi',
 'tu',
 'leur',
 'sans',
 'être',
 'm’',
 'vouloir',
 'savoir',
 'où',
 'venir',
 'homme',
 'autre',
 'ou',
 'à',
 'petit',
 'quelque',
 'prendre',
 'grand',
 'encore',
 'votre',
 'femme',
 'rien',
 'quand',
 'là',
 'main',
 'peu',
 'jour',
 'celui',
 'dont',
 'bon',
 'mettre',
 'aussi',
 'jeune',
 'heure',
 'cela',
 'devoir',
 'falloir',
 'été',
 'non',
 'croire',
 'temps',
 'oeil',
 'puis',
 'chose',
 'donc',
 'sous',
 'ça',
 'jamais',
 'Monsieur',
 'fois',
 'toujours',
 'passer',
 'notre',
 'après',
 'seul',
 'ton',
 'tête',
 'alors',
 'porte',
 'entendre',


In [13]:
bigram_lemma_selected

['de_le',
 'dans_le',
 'd’_un',
 'qu’_il',
 'de_son',
 'à_le',
 'c’_être',
 'et_le',
 'sur_le',
 'que_le',
 'de_l’',
 'n’_avoir',
 'il_avoir',
 'et_de',
 'de_ce',
 'que_je',
 'j’_avoir',
 'tout_le',
 'je_ne',
 'y_avoir',
 'à_l’',
 'qu’_lui',
 'lui_avoir',
 'avoir_pas',
 'à_son',
 'par_le',
 'dans_un',
 'il_être',
 'il_ne',
 'avec_un',
 'avoir_un',
 'il_y',
 'il_se',
 'pour_le',
 'dans_son',
 'il_n’',
 'être_pas',
 'l’_avoir',
 'que_vous',
 'n’_être',
 'comme_un',
 'être_un',
 'je_être',
 'le_plus',
 'ne_pouvoir',
 'je_vous',
 'à_ce',
 'ce_être',
 'qu’_on',
 'et_il',
 'à_un',
 'vous_avoir',
 'de_mon',
 'c’_éter',
 'avoir_été',
 'un_peu',
 'il_falloir',
 'ce_que',
 'qui_avoir',
 'le_main',
 'de_tout',
 'je_me',
 'être_-ce',
 'avoir_le',
 'être_le',
 'et_je',
 'dire_il',
 'il_s’',
 'm’_avoir',
 'pas_de',
 'par_un',
 '-_être',
 'je_n’',
 'pouvoir_-',
 'qu’_un',
 'faire_un',
 'pas_le',
 'avoir_faire',
 'le_porte',
 'que_ce',
 'sur_son',
 'ce_qui',
 'avec_le',
 'dans_l’',
 'il_éter

In [19]:
def moulinette(path_name, list_lemma_select, list_bigram_lemma_select):
    """fonction main qui utilise les fonctions précédentes et tourne sur le corpus"""
    
    nombre_total_tokens = 0
 
    dict_results = {}

    df_main = pd.DataFrame()
    
    print("\n\nBEGIN PROCESSING CORPUS-----------")
    
    for doc in glob(path_name):
        
        print("\n\nBEGIN PROCESSING NOVEL-----------")

        doc_name = path.splitext(path.basename(doc))[0]
        print(doc_name)
        
        #On recupere le texte des romans sous forme de listes de lemmes grâce à spacy
        
        list_lemma_temp, nombre_tokens = pipeline_spacy(doc)
        
        print("PIPELINE SPACY ----------- OK")
        
        print("NOMBRE TOKENS = ", nombre_tokens)
        
        nombre_total_tokens += nombre_tokens
        
        list_bigram_lemma_temp = bigrammize(list_lemma_temp)
        
        dict_results.update(dict_freq_token(list_lemma_select, list_lemma_temp))
        dict_results.update(dict_freq_token(list_bigram_lemma_select, list_bigram_lemma_temp))
        
        dict_results["index"] = doc_name
        
        df_temp = pd.DataFrame(dict_results, index=[0])
        
        df_main = df_main.append(df_temp, ignore_index = True)
        
        print("PROCESS RESULTS ----------- OK")

        print("END PROCESSING NOVEL --------------\n\n")
        print("PROGRESSION ", round(nombre_total_tokens/31857823,2),'% COMPLETED\n')#*100 round 4
        
    df_main.set_index("index", inplace = True)
    
    print("\n NOMBRE TOTAL TOKENS = ", nombre_total_tokens)   
    print("\n\n END PROCESSING CORPUS --------------\n\n")
    
    
    return df_main

In [20]:
df_main = moulinette(path_name, lemma_selected, bigram_lemma_selected)



BEGIN PROCESSING CORPUS-----------


BEGIN PROCESSING NOVEL-----------
1861_Veilles-comtesse-de_Sagesse-et-bonte-livre-des-jeunes-personnes_noncanon_CHUNK_38
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1066
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1859_Feval-Paul-(pere)_Le-Roi-des-gueux_noncanon_CHUNK_67
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1068
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1850_Dumas-Alexandre_Le-Vicomte-de-Bragelonne_canon_CHUNK_508
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1074
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1857_Feval-Paul-(pere)_Le-Bossu_noncanon_CHUNK_69
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1016
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL -----

PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1059
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1859_Ulbach-Louis_Pauline-Foucault_noncanon_CHUNK_63
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1072
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1853_Desnoiresterres-Gustave_Un-amour-en-diligence_noncanon_CHUNK_5
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1065
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1865_Ponson-du-Terrail-Pierre_Le-Chambrion_noncanon_CHUNK_19
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1048
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1879_Huysmans-Joris-Karl_Les-soeurs-Vatard_canon_CHUNK_50
PIPELINE SPA

PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1020
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1858_Sand-George_Les-beaux-messieurs-de-Bois-Dore-2_canon_CHUNK_19
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1014
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1857_About-Edmond_Germaine_noncanon_CHUNK_71
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1057
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1862_Pont-Jest-Rene-de_Bolino-le-negrier-souvenirs-de-l-Ocean-Indien_noncanon_CHUNK_37
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1069
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1862_Malot-Hector_Les-Amants_noncanon_CHUNK_81
PIPELI

PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1069
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1856_Feval-Paul-(pere)_Madame-Gil-Blas-souvenirs-et-aventures-d-une-femme-de-notre-temps-(Volume-1)_noncanon_CHUNK_20
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1048
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1861_Gondrecourt-Aristide-de_Le-Pays-de-la-peur-tome-3_noncanon_CHUNK_26
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1057
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1857_Dumas-Alexandre_Le-meneur-de-loups_canon_CHUNK_74
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1052
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1878_L

PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1861_Villars-Fanny_Marie-et-Marguerite-histoire-du-XIIIe-siecle_noncanon_CHUNK_31
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1060
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1850_Dumas-Alexandre_Le-Vicomte-de-Bragelonne_canon_CHUNK_658
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1073
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1862_Feval-Paul-(pere)_Les-habits-noirs-Tome-I_noncanon_CHUNK_9
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1053
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.0 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1864_Boissieres-Ernest_Un-crime-inconnu_noncanon_CHUNK_6
PIPELINE SPACY ----------- OK
NOMBRE TO

...

PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1862_Chevalier-H-Emile_La-Capitaine_noncanon_CHUNK_26
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1068
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1865_Ponson-du-Terrail-Pierre-Alexis-de_Le-Castel-du-Diable_noncanon_CHUNK_42
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1065
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1863_Nyon-Eugene_La-Reine-de-Jerusalem_noncanon_CHUNK_61
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1076
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1850_Dumas-Alexandre_Le-Vicomte-de-Bragelonne_canon_CHUNK_27
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  105

PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1852_Dumas-Alexandre_La-comtesse-de-Charny_canon_CHUNK_472
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1071
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1859_Ulbach-Louis_Pauline-Foucault_noncanon_CHUNK_126
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1064
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1884_Zola-Emile_La-joie-de-vivre_canon_CHUNK_68
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1062
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1854_Dumas-Alexandre-Pere_Les-Mohicans-de-Paris-5_canon_CHUNK_66
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1061
PROCESS RESULTS ------

PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1877_Verne-Jules_Hector-Servadac-Voyages-et-aventures-a-travers-le-monde-solaire_canon_CHUNK_55
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1051
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1862_Hugo-Victor_Les-Miserables_canon_CHUNK_73
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1063
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1850_Feval-Paul-(pere)_Les-Belles-de-nuit-ou-Les-Anges-de-la-famille-Tome-I_noncanon_CHUNK_70
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1067
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1874_Zola-Emile_La-conquete-de-Plassans_canon_CHUNK_61
PIPELINE

PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1854_Dumas-Alexandre-Pere_Les-Mohicans-de-Paris-5_canon_CHUNK_25
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1051
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.49 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1852_Ponson-du-Terrail-Pierre_Les-Cavaliers-de-la-nuit_noncanon_CHUNK_129
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1060
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.5 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1881_Daudet-Alphonse_Numa-Roumestan_canon_CHUNK_9
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1056
PROCESS RESULTS ----------- OK
END PROCESSING NOVEL --------------


PROGRESSION  0.5 % COMPLETED



BEGIN PROCESSING NOVEL-----------
1855_Reybaud-Louis_La-vie-de-l-employe_noncanon_CHUNK_69
PIPELINE SPACY ----------- OK
NOMBRE TOKENS =  1070
PROC

KeyboardInterrupt: 

In [ ]:
df_main

In [ ]:
df_main.to_csv(r'chunks_BoW_features.csv', index = True)